In [1]:
import sys
sys.path.append('/home/dp/Desktop/Bit/Bit_BP_new/')
from Get_available_gpus import get_available_gpus
print(get_available_gpus())

The following GPU devices ara available: ['/device:GPU:0', '/device:GPU:1', '/device:GPU:2', '/device:GPU:3', '/device:GPU:4', '/device:GPU:5'] 
 Number of gpus : 6
None


In [2]:
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import warnings
warnings.filterwarnings("ignore")
from sklearn.model_selection import train_test_split
from sklearn.decomposition import PCA
import random
import keras
from keras.models import Sequential,Model
from keras.layers import Dense, Activation, Flatten, Convolution1D, Dropout,Input
from keras.layers import BatchNormalization,MaxPooling1D,concatenate
from keras.utils import np_utils,multi_gpu_model
from keras.callbacks import ModelCheckpoint
from keras import regularizers
from sklearn.cluster import KMeans
from scipy import stats
from sklearn import preprocessing
from keras import backend as bek
import gc
%matplotlib inline

Using TensorFlow backend.


In [3]:
# """
# data cell
# """
# df1=pd.read_csv('/home/dp/Desktop/Bit/datapath/pair_end_merge_SYS_random_400_split_up.csv',index_col=0)## SYS



In [4]:
# for i,item in enumerate(df1['SYS']):
#     '''
#     Repleace SYS by DIA when you run diastolic
#     '''
#     if(df1['time'].iloc[i]==2):
#         continue
#     elif(df1['time'].iloc[i]==1):
#         temp=df1[(df1['Person No']==df1['Person No'].iloc[i])&(df1['time']==2)]['SYS']
#         if(temp.empty):
#             continue
#         else:
#             print(df1['SYS'].iloc[i],temp.iloc[0])
#             df1['SYS'].iloc[i]=temp.iloc[0]
#     else:
#         continue

In [5]:
# cond2 = df1['count']!=0
# df1 = df1[cond2]

# #normalize
# target = 'SYS'# DIA

In [6]:
df1=pd.read_csv('/home/dp/Desktop/Bit/Bit_BP_new/datapath/pair_end_merge_SYS_random_400_split_up_hybrid_database.csv', index_col=0)

target = 'SYS'

print(df1.shape)

(84064, 831)


In [7]:
batch_s = 3000
n_epochs = 1000

In [8]:
'''
model cell
'''
def base_model():
    in_s = Input((406, 1))
    model_s = Convolution1D(nb_filter=256, filter_length=3) (in_s)
    model_s = BatchNormalization(axis=-1)(model_s)
    model_s = Activation('relu')(model_s)
    model_s = MaxPooling1D(pool_size=2)(model_s)
    
    model_s = Convolution1D(nb_filter=256, filter_length=3) (model_s)
    model_s = BatchNormalization(axis=-1)(model_s)
    model_s = Activation('relu')(model_s)
    model_s = MaxPooling1D(pool_size=2)(model_s)
    
    model_s = Convolution1D(nb_filter=512, filter_length=3) (model_s)
    model_s = BatchNormalization(axis=-1)(model_s)
    model_s = Activation('relu')(model_s)
    model_s = MaxPooling1D(pool_size=2)(model_s)
    
    model_s = Convolution1D(nb_filter=1024, filter_length=3) (model_s)
    model_s = BatchNormalization(axis=-1)(model_s)
    model_s = Activation('relu')(model_s)
    model_s = MaxPooling1D(pool_size=2)(model_s)
    
    model_s = Convolution1D(nb_filter=2048, filter_length=3) (model_s)
    model_s = BatchNormalization(axis=-1)(model_s)
    model_s = Activation('relu')(model_s)
    model_s = MaxPooling1D(pool_size=2)(model_s)
    
    model_s = Flatten()(model_s)
    
    '''
    input1 = keras.layers.Input(shape=(1,))
    c = keras.layers.Concatenate(axis=-1)([model_s, input1])
    '''
    m = BatchNormalization(axis=-1)(model_s)
    m = Dense(4096,activation='relu')(m)
    m = Dense(2048,activation='relu')(m)
    out = Dense(1,activation='linear')(m)
    
    model = Model(inputs=[in_s], outputs=[out])
    
    adam=keras.optimizers.Adam(lr=0.00001, beta_1=0.9, beta_2=0.999)
    model = multi_gpu_model(model,gpus=6)
    model.compile(loss='mean_squared_error', optimizer='adam')
    return model

In [9]:
def test_step(train_temp,valid_temp, test_temp, testNo_temp, testtime_temp):
    X_train_s = train_temp.iloc[:,17:423]
    X_valid_s = valid_temp.iloc[:,17:423]
    X_test_s = test_temp.iloc[:,17:423]
    '''
    Training data
    '''
    
    f1=['SYS']
    Y_train = train_temp[f1]
    Y_train = scalert.transform(Y_train)
    
    # reshape train data
    X_train_r_s = np.zeros((len(X_train_s), 406, 1))
    X_train_r_s[:, :, 0] = X_train_s
    
    '''
    Validation data
    '''
    f2 = ['SYS']
    Y_valid = valid_temp[f2]
    Y_valid = scalert.transform(Y_valid)
    
    # reshape validation data
    X_valid_r_s = np.zeros((len(X_valid_s), 406, 1))
    X_valid_r_s[:,:,0] = X_valid_s
    
    ''' testing data'''
    # reshape testing data
    X_test_r_s = np.zeros((len(X_test_s), 406, 1))
    X_test_r_s[:, :, 0] = X_test_s
    

    #fit
    '''
    - if directory for saving weight not exist, create a directory using testing subject number
    - each test subject best weight is saved with a file name with person number and round
    '''
    saveweight_path = os.makedirs('BestWeights/Person_' + str(testNo_temp),exist_ok=True)
    filepath='BestWeights/Person_' + str(testNo_temp) +'/'+ 'weights_best_Person_' + str(testNo_temp)+'_round_' + str(testtime_temp)+'.hdf5'
    checkpoint = ModelCheckpoint(filepath, monitor='loss', verbose=1, save_best_only=True,mode='min')
    callbacks_list = [checkpoint]
    
    model= base_model()
    history = model.fit([X_train_r_s], Y_train, epochs=n_epochs, batch_size=batch_s, validation_data=(X_valid_r_s, Y_valid),  callbacks=callbacks_list,verbose=2)
    ### Save loss values
    df_loss = pd.DataFrame(history.history)
    ### loss path
    '''
    - if directory for saving train and validation loss not exist, create a directory using testing subject number
    - each training loss for each testing person and round is save with a file name indicating person number and rounds
    '''
    saveloss_path = os.makedirs('Loss_results/Person_' + str(testNo_temp),exist_ok=True)
    file_name='Loss_results/Person_' + str(testNo_temp) +'/'+ 'train_valid_loss_sys_Person_' + str(testNo_temp)+'_round_' + str(testtime_temp)+'.csv'
    df_loss.to_csv(file_name, index = False)

    
    test_pred = model.predict([X_test_r_s])
    test_pred1 = scalert.inverse_transform(test_pred)
    test_temp['SYS_p']=test_pred1
    
    temp_a=0
    temp_b=0
    test_SYS_r=[]
    test_SYS_p=[]

    
    for i,item in enumerate(test_temp['Person No']):
        if((test_temp['Person No'].iloc[i]!=temp_a) | (test_temp['time'].iloc[i]!=temp_b)):
            
            #administrator mode
            test_SYS_r.append(test_temp['SYS'].iloc[i])
            temp = test_temp[(test_temp['Person No']==test_temp['Person No'].iloc[i])&(test_temp['time']==test_temp['time'].iloc[i])]
            t = np.median(temp['SYS_p'])
            test_SYS_p.append(t)
            temp_a = test_temp['Person No'].iloc[i]
            temp_b = test_temp['time'].iloc[i]

            
    print(test_SYS_p)
    print(test_SYS_r)
    del model
    bek.clear_session()
    gc.collect()
    return (test_SYS_p,test_SYS_r)

In [10]:
def test_step1(train_temp,valid_temp, test_temp, testNo_temp, testtime_temp):
    
    X_train_s = train_temp.iloc[:,17:423]
    X_valid_s = valid_temp.iloc[:,17:423]
    X_test_s = test_temp.iloc[:,17:423]
    '''
    Training data
    '''
    f1=['SYS']
    Y_train = train_temp[f1]
    Y_train = scalert.transform(Y_train)
    
    # reshape train data
    X_train_r_s = np.zeros((len(X_train_s), 406, 1))
    X_train_r_s[:, :, 0] = X_train_s
    
    '''
    Validation data
    '''
    f2 = ['SYS']
    Y_valid = valid_temp[f2]
    Y_valid = scalert.transform(Y_valid)
    
    # reshape validation data
    X_valid_r_s = np.zeros((len(X_valid_s), 406, 1))
    X_valid_r_s[:,:,0] = X_valid_s
    
    '''
    testing data
    '''
    # reshape test data
    X_test_r_s = np.zeros((len(X_test_s), 406, 1))
    X_test_r_s[:, :, 0] = X_test_s
    
    #fit
    
    model1=base_model()
    '''
    - call each test subject best weight in the saved directory with a file name as a person number and round
    '''
    filepath_='BestWeights/Person_' + str(testNo_temp) +'/'+ 'weights_best_Person_' + str(testNo_temp)+'_round_' + str(testtime_temp)+'.hdf5'
    #model1.load_weights('weights_best.hdf5', by_name = True)
    model1.load_weights(filepath_, by_name = True)

    
    test_pred = model1.predict([X_test_r_s])
    test_pred1 = scalert.inverse_transform(test_pred)
    test_temp['SYS_p']=test_pred1
    
    temp_a=0
    temp_b=0
    test_SYS_r=[]
    test_SYS_p=[]

    
    for i,item in enumerate(test_temp['Person No']):
        if((test_temp['Person No'].iloc[i]!=temp_a) | (test_temp['time'].iloc[i]!=temp_b)):
            
            #administrator mode
            test_SYS_r.append(test_temp['SYS'].iloc[i])
            temp = test_temp[(test_temp['Person No']==test_temp['Person No'].iloc[i])&(test_temp['time']==test_temp['time'].iloc[i])]
            t = np.median(temp['SYS_p'])
            test_SYS_p.append(t)
            temp_a = test_temp['Person No'].iloc[i]
            temp_b = test_temp['time'].iloc[i]

            
    print(test_SYS_p)
    print(test_SYS_r)
    
    #del model1
    bek.clear_session()
    gc.collect()
    
    return (test_SYS_p,test_SYS_r)

In [11]:
################
testingNo_all = [1273,543,1002,342,245,149,1888,1373,1020,1775,1598, 1436, 1722, 2095, 2096]
################



for testingNo in testingNo_all:

    test_p=[]
    test_r=[]
    
    test_p_best=[]
    test_r_best=[]

    for test_time in range(10,16):
        test  = df1[(df1['count']==testingNo)&(df1['count_time']==test_time)]
        train = df1
        if (test.empty):
            continue
        else:
            test_data_future = df1[(df1['count']==testingNo)&(df1['count_time']>=test_time)]
            print(f'future data shape : {test_data_future.shape}')
            test_data_future_index = test_data_future.index
            train = train.drop(test_data_future_index)
            print(f'Train shape : {train.shape}')
            #print('Train shape : ', train.shape[0] + test.shape[0])
            '''
            - Choose a validation set
            - validation set is selected from subjects having rounds >=8
            - from subjects round 8 to 11, the last round is considered as a validation set
            - from subjects with rounds 12 and above, the last two successive rounds were considered as a validation set
            '''
            persons_last_round8 = set(train[train['count_time']>=8]['count'])-set(train[train['count_time']>=9]['count'])
            persons_last_round9 = set(train[train['count_time']>=9]['count'])-set(train[train['count_time']>=10]['count'])
            persons_last_round10 = set(train[train['count_time']>=10]['count'])-set(train[train['count_time']>=11]['count'])
            persons_last_round11 = set(train[train['count_time']>=11]['count'])-set(train[train['count_time']>=12]['count'])
            persons_last_round12 = set(train[train['count_time']>=12]['count'])-set(train[train['count_time']>=13]['count'])
            persons_last_round13 = set(train[train['count_time']>=13]['count'])-set(train[train['count_time']>=14]['count'])
            persons_last_round14 = set(train[train['count_time']>=14]['count'])-set(train[train['count_time']>=15]['count'])
            persons_last_round15 = set(train[train['count_time']>=15]['count'])
            validation = []
            for valid_person8 in persons_last_round8:
                valid8 = train[(train['count'] == valid_person8)&(train['count_time']==8)]
                validation.append(valid8)
            for valid_person9 in persons_last_round9:
                valid9 = train[(train['count'] == valid_person9)&(train['count_time']==9)]
                validation.append(valid9)
            for valid_person10 in persons_last_round10:
                valid10 = train[(train['count'] == valid_person10)&(train['count_time']==10)]
                validation.append(valid10)
            for valid_person11 in persons_last_round11:
                valid11 = train[(train['count'] == valid_person11)&(train['count_time']==11)]
                validation.append(valid11)
            for valid_person12 in persons_last_round12:
                valid12 = train[(train['count'] == valid_person12)&(train['count_time']>=11)]
                validation.append(valid12)
            for valid_person13 in persons_last_round13:
                valid13 = train[(train['count'] == valid_person13)&(train['count_time']>=12)]
                validation.append(valid13)
            for valid_person14 in persons_last_round14:
                valid14 = train[(train['count'] == valid_person14)&(train['count_time']>=13)]
                validation.append(valid14)
            for valid_person15 in persons_last_round15:
                valid15 = train[(train['count'] == valid_person15)&(train['count_time']>=14)]
                validation.append(valid15)
            validation_data = pd.concat(validation)
            validation_data_index = validation_data.index
            train = train.drop(validation_data_index)
            t = train[target]
            t = t.values.reshape(-1, 1)
            scalert = preprocessing.MinMaxScaler().fit(t)
            (temp_pred,temp_real) = test_step(train,validation_data, test,testingNo,test_time)
            (temp_pred_best,temp_real_best) = test_step1(train,validation_data,test,testingNo,test_time)
            
            test_p.append(temp_pred)
            test_r.append(temp_real)
            
            test_p_best.append(temp_pred_best)
            test_r_best.append(temp_real_best)
            
    d = {'SYS_real': test_r, 'SYS_pred': test_p}
    df_f = pd.DataFrame(data = d)
    
    ind =[]
    for j in range(2,len(df_f.index)+2):
        ind.append(j)
    
    df_f.index=ind
    
    name_temp =str(testingNo)+'-1000-256.csv'
    df_f.to_csv('SYS/' +name_temp)
    
    
    d_best = {'SYS_real': test_r_best, 'SYS_pred': test_p_best}
    df_f_best = pd.DataFrame(data = d_best)
    
    ind =[]
    for j in range(2,len(df_f_best.index)+2):
        ind.append(j)
    
    df_f_best.index=ind
    
    name_temp_best =str(testingNo)+'-1000-256-best.csv'
    df_f_best.to_csv('SYS/' +name_temp_best)

future data shape : (1091, 831)
Train shape : (82973, 831)
Train on 78871 samples, validate on 4102 samples
Epoch 1/1000
 - 37s - loss: 461.6219 - val_loss: 0.3809

Epoch 00001: loss improved from inf to 461.62188, saving model to BestWeights/Person_1273/weights_best_Person_1273_round_10.hdf5
Epoch 2/1000
 - 13s - loss: 0.0477 - val_loss: 0.1348

Epoch 00002: loss improved from 461.62188 to 0.04771, saving model to BestWeights/Person_1273/weights_best_Person_1273_round_10.hdf5
Epoch 3/1000
 - 13s - loss: 0.0326 - val_loss: 0.0640

Epoch 00003: loss improved from 0.04771 to 0.03256, saving model to BestWeights/Person_1273/weights_best_Person_1273_round_10.hdf5
Epoch 4/1000
 - 13s - loss: 0.0299 - val_loss: 0.0511

Epoch 00004: loss improved from 0.03256 to 0.02994, saving model to BestWeights/Person_1273/weights_best_Person_1273_round_10.hdf5
Epoch 5/1000
 - 13s - loss: 0.0293 - val_loss: 0.0509

Epoch 00005: loss improved from 0.02994 to 0.02928, saving model to BestWeights/Person_1273

In [12]:
# def extract_Train_test(df, testingNo):
#     test_data = []
#     train_data = []
#     for test_time in range(10,16):
#         test  = df[(df['count']==testingNo)&(df['count_time']==test_time)]
#         train = df1
#         if (test.empty):
#             continue
#         else:
#             test_data_future = df[(df['count']==testingNo)&(df['count_time']>=test_time)]
#             print(f'future data shape : {test_data_future.shape}')
#             test_data_future_index = test_data_future.index
#             train = train.drop(test_data_future_index)
#             print(f'Train shape : {train.shape}')
#             #print('Train shape : ', train.shape[0] + test.shape[0])
#             '''
#             - Choose a validation set
#             '''
#             persons_last_round8 = set(train[train['count_time']>=8]['count']) - set(train[train['count_time']>=9]['count'])
#             persons_last_round9 = set(train[train['count_time']>=9]['count']) - set(train[train['count_time']>=10]['count'])
#             persons_last_round10 = set(train[train['count_time']>=10]['count']) - set(train[train['count_time']>=11]['count'])
#             persons_last_round11 = set(train[train['count_time']>=11]['count']) - set(train[train['count_time']>=12]['count'])
#             persons_last_round12 = set(train[train['count_time']>=12]['count']) - set(train[train['count_time']>=13]['count'])
#             persons_last_round13 = set(train[train['count_time']>=13]['count']) - set(train[train['count_time']>=14]['count'])
#             persons_last_round14 = set(train[train['count_time']>=14]['count']) - set(train[train['count_time']>=15]['count'])
#             persons_last_round15 = set(train[train['count_time']>=15]['count'])
#             validation = []
#             for valid_person8 in persons_last_round8:
#                 valid8 = train[(train['count'] == valid_person8)&(train['count_time']==8)]
#                 validation.append(valid8)
#             for valid_person9 in persons_last_round9:
#                 valid9 = train[(train['count'] == valid_person9)&(train['count_time']==9)]
#                 validation.append(valid9)
#             for valid_person10 in persons_last_round10:
#                 valid10 = train[(train['count'] == valid_person10)&(train['count_time']==10)]
#                 validation.append(valid10)
#             for valid_person11 in persons_last_round11:
#                 valid11 = train[(train['count'] == valid_person11)&(train['count_time']==11)]
#                 validation.append(valid11)
#             for valid_person12 in persons_last_round12:
#                 valid12 = train[(train['count'] == valid_person12)&(train['count_time']>=11)]
#                 validation.append(valid12)
#             for valid_person13 in persons_last_round13:
#                 valid13 = train[(train['count'] == valid_person13)&(train['count_time']>=12)]
#                 validation.append(valid13)
#             for valid_person14 in persons_last_round14:
#                 valid14 = train[(train['count'] == valid_person14)&(train['count_time']>=13)]
#                 validation.append(valid14)
#             for valid_person15 in persons_last_round15:
#                 valid15 = train[(train['count'] == valid_person15)&(train['count_time']>=14)]
#                 validation.append(valid15)
#             validation_data = pd.concat(validation)
#             validation_data_index = validation_data.index
#             train = train.drop(validation_data_index)
#             print('Train and valid shape : ', train.shape[0] + validation_data.shape[0])
#             print(f'Train and validation shape, {train.shape}, {validation_data.shape}')
#             train_data.append(train)
#             test_data.append(test)
#     return train_data, test_data, validation